In [44]:
from leagues.models import Competition,Season
from base_app.helpers import best_fuzzy_match
from games.models import Game
from datetime import datetime
import pandas as pd
import numpy as np
import os

In [45]:
EV_PATH = "D:\MetaData"
ST_PATH = "D:\MetaData-shot"

In [46]:
event_files = []
for base,_,files in os.walk(EV_PATH):
    for f in files:
        if 'shot' not in f :
            event_files.append(f"{base}\{f}")

shot_files = []
for base,_,files in os.walk(ST_PATH):
    for f in files:
        shot_files.append(f"{base}\{f}")

event_files = list(set(event_files))
shot_files = list(set(shot_files))


In [47]:
len(event_files),len(shot_files)

(547, 199)

In [48]:
map_example = []
non_mapped_season = []
for season in Season.objects.all():
    conf = season.competition.confederation
    region = season.competition.country
    
    e_name = season.competition.name_scoresaway.replace(' ','_').replace(".","")
    s_name = season.competition.name_fotmob.replace(' ','_').replace(".","")
    
    e_s_name = season.name.replace('/','_').replace(' ','_')
    s_s_name = season.name_fotmob.replace('/','_').replace(' - ','_')

    if season.competition_id == 27 :
        e_search_str = f"D:\\MetaData\\{conf}\\{region}\\{e_name}_{e_s_name}_events.xlsx"
        s_search_str = [f"D:\\MetaData-shot\\{conf}\\{region}\\{s_name}_{e_s_name}_Apertura_shots.xlsx",
                        f"D:\\MetaData-shot\\{conf}\\{region}\\{s_name}_{e_s_name}_Clausura_shots.xlsx"]
        if e_search_str in event_files and s_search_str[0] in shot_files and s_search_str[1] in shot_files  :
            map_example.append((season,e_search_str,"__||__".join(s_search_str)))
    else:
        e_search_str = f"D:\\MetaData\\{conf}\\{region}\\{e_name}_{e_s_name}_events.xlsx"
        s_search_str = f"D:\\MetaData-shot\\{conf}\\{region}\\{s_name}_{s_s_name}_shots.xlsx"

    if e_search_str in event_files and s_search_str in shot_files  :
        map_example.append((season,e_search_str,s_search_str))
    else:
        non_mapped_season.append((season,e_search_str))

In [49]:
len(map_example),len(non_mapped_season)

(199, 381)

In [50]:
from datetime import timedelta
                               # e_df,s_df,event_teams,shot_teams,mapping_dict,8,return_counts=True
def match_and_count_for_season(e_df,s_df,event_teams,shot_teams,hrs,return_counts=False):
    max_diff_hours = hrs
    results = []
    merged = []
    corr = 0
    wrong = 0
    ups = 0
    not_req = 0
    min_dt_of_event = s_df['datetime'].min()
    for i, row in e_df.iterrows():
        e_home = row['home_team']
        e_away = row['away_team']
        e_date = row['datetime']

        if (e_date-min_dt_of_event).total_seconds()/3600 < -8 :
            not_req+=1
            continue
        fuzzy_home = best_fuzzy_match(e_home, shot_teams,threshold_multi=75)
        fuzzy_away = best_fuzzy_match(e_away, shot_teams,threshold_multi=75)
        
        # Get top fuzzy keys (most probable names)
        possible_homes = list(fuzzy_home.keys())
        possible_aways = list(fuzzy_away.keys())
        
        # Check all possible home-away combinations in df
        mask = (
            (s_df['home_team'].isin(possible_homes)) &
            (s_df['away_team'].isin(possible_aways)) &
            (abs(s_df['datetime'] - e_date) <= timedelta(hours=max_diff_hours))
        )
        
        matches = s_df[mask]
        if matches.shape[0] >1:
            print("fakk, there are more ... do something kent saab")
            # print(f"\n{e_home} -> {fuzzy_home}")
            # print(f"{e_away} -> {fuzzy_away}")
            # print(f"datetime : {e_date} \n\n")
            
            # ups+=1
            fuzzy_home = best_fuzzy_match(e_home, shot_teams,threshold_multi=85)
            fuzzy_away = best_fuzzy_match(e_away, shot_teams,threshold_multi=85)
            
            # Get top fuzzy keys (most probable names)
            possible_homes = list(fuzzy_home.keys())
            possible_aways = list(fuzzy_away.keys())
            
            # Check all possible home-away combinations in df
            mask = (
                (s_df['home_team'].isin(possible_homes)) &
                (s_df['away_team'].isin(possible_aways)) &
                (abs(s_df['datetime'] - e_date) <= timedelta(hours=max_diff_hours))
            )
            
            matches = s_df[mask]
            if matches.shape[0] > 1 :
                print("Fadd lo bhai hun dooji waar!!!!!!!!!!")
                print(f"\n{e_home} -> {fuzzy_home}")
                print(f"{e_away} -> {fuzzy_away}")
                print(f"datetime : {e_date} \n\n")
                ups+=1
                
        # print(f"Found {matches.shape[0]} matched for the fuzzy map combinations")
        # print(f"\n{e_home} -> {fuzzy_home}")
        # print(f"{e_away} -> {fuzzy_away}")
        # print(f"datetime : {e_date}")
        if not matches.empty:
            correct_match = matches.iloc[0]
                    
            temp = {}
            temp['e_home_team'] = e_home
            temp['s_home_team'] = correct_match['home_team']
            
            temp['e_away_team'] = e_away
            temp['s_away_team'] = correct_match['away_team']
        
            temp['e_datetime'] = e_date
            temp['s_datetime'] = correct_match['datetime']
        
            temp['event_url'] = row['event_url']
            temp['shot_url'] = correct_match['shot_url']
            merged.append(temp) 
            corr+=1
        else:
            # print("\n Adding Blanks \n")
            temp = {}
            temp['e_home_team'] = e_home
            temp['s_home_team'] = "NA"
            
            temp['e_away_team'] = e_away
            temp['s_away_team'] = "NA"
        
            temp['e_datetime'] = e_date
            temp['s_datetime'] = "NA"
        
            temp['event_url'] = row['event_url']
            temp['shot_url'] = "NA"
            merged.append(temp) 
            if fuzzy_home == {} or fuzzy_away == {} :
            
                # print(row)
                # print()
                print(f"\nF : {e_home} -> {fuzzy_home}")
                print(f"{e_away} -> {fuzzy_away}")
                print(f"datetime : {e_date}")
                print(f"Diff : {e_date-min_dt_of_event} \n")
            else:
                print(f" S : \n{e_home} -> {fuzzy_home}")
                print(f"{e_away} -> {fuzzy_away}")
                print(f"datetime : {e_date}")
                print(f"Min Dt : {min_dt_of_event}")
            
            wrong+=1
            print("❌ No close match found.")
        # if corr+wrong+ups != len(merged):
        #     print(f"{corr}+{wrong}+{ups} != {len(merged)}\n")
        #     print(row)
    if return_counts :
        return corr,wrong,ups
    return pd.DataFrame(merged),corr,wrong,ups
# results_df = pd.DataFrame(results)

## Phase 1 : Add whatever is there

non mapped

In [51]:
errs = []
totals = 0
for i,(season,event_path) in enumerate(non_mapped_season,1) :
    try :
    
        ev_df = pd.read_excel(event_path)
        print(f"\nWorking on season no: {i} having {ev_df.shape[0]} rows\n")
        for n,(j,row) in enumerate(ev_df.iterrows(),1):
            totals+=1
            obj,created = Game.objects.get_or_create(
                    season = season,
                    home_team = row.get('home_team'),
                    away_team = row.get('away_team'),
                    match_date = datetime.strptime(str(row.get('datetime')),"%Y-%m-%d %H:%M:%S"),
                    game_event_url = row.get('event_url')
            )
            if created is False :
                existing.append({
                    season : season,
                    home_team : row.get('home_team'),
                    away_team : row.get('away_team'),
                    match_date : datetime.strptime(str(row.get('datetime')),"%Y-%m-%d %H:%M:%S"),
                    game_event_url : row.get('event_url')
                })
            # obj.save()
    except Exception as e :
        temp = {}
        temp['row'] = row
        temp['ev_path'] = event_path
        temp['exception'] = e
        errs.append(temp)
    # break


Working on season no: 1 having 112 rows


Working on season no: 2 having 152 rows


Working on season no: 3 having 134 rows


Working on season no: 4 having 139 rows


Working on season no: 5 having 102 rows


Working on season no: 6 having 135 rows


Working on season no: 7 having 135 rows


Working on season no: 8 having 119 rows



D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2025-05-03 22:00:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2024-05-25 21:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2023-05-06 14:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2021-11-23 21:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\d


Working on season no: 9 having 117 rows


Working on season no: 10 having 61 rows


Working on season no: 11 having 43 rows


Working on season no: 12 having 36 rows


Working on season no: 13 having 127 rows


Working on season no: 14 having 127 rows


Working on season no: 18 having 132 rows


Working on season no: 19 having 132 rows


Working on season no: 20 having 132 rows



D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2024-05-05 21:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2022-10-22 16:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2021-11-05 21:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2020-03-11 19:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\d


Working on season no: 21 having 132 rows


Working on season no: 22 having 132 rows


Working on season no: 23 having 0 rows


Working on season no: 24 having 0 rows


Working on season no: 25 having 0 rows


Working on season no: 26 having 240 rows


Working on season no: 27 having 240 rows


Working on season no: 28 having 240 rows



...

D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2024-05-30 22:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2023-06-08 22:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2022-06-02 22:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2021-05-26 22:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\d


Working on season no: 375 having 337 rows


Working on season no: 376 having 340 rows


Working on season no: 377 having 342 rows


Working on season no: 378 having 342 rows



D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2025-05-26 06:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2024-05-27 06:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2023-05-29 07:05:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2022-05-30 06:40:00) while time zone support is active.
  warnings.warn(



Working on season no: 379 having 342 rows


Working on season no: 380 having 268 rows


Working on season no: 381 having 328 rows



D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2021-05-31 06:45:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2019-12-30 07:45:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2019-05-27 06:36:00) while time zone support is active.
  warnings.warn(


In [54]:
len(errs),len(existing),len(non_mapped_season)

(284, 265, 381)

In [41]:
t = []
for x in non_mapped_season :
    print(x)
    o = {}
    p = pd.read_excel(x[1])
    o['Comp'] = x[0].competition.competition_name
    o['cnt'] = p.shape[0]
    t.append(o)

(<Season: AFC Champions League - 2024/2025 - FM(2024/2025)>, 'D:\\MetaData\\AFC\\AFC\\AFC_Champions_League_Elite_2024_2025_events.xlsx')
(<Season: AFC Champions League - 2023/2024 - FM(2023/2024)>, 'D:\\MetaData\\AFC\\AFC\\AFC_Champions_League_Elite_2023_2024_events.xlsx')
(<Season: AFC Champions League - 2022 - FM(2022)>, 'D:\\MetaData\\AFC\\AFC\\AFC_Champions_League_Elite_2022_events.xlsx')
(<Season: AFC Champions League - 2021 - FM(2021)>, 'D:\\MetaData\\AFC\\AFC\\AFC_Champions_League_Elite_2021_events.xlsx')
(<Season: AFC Champions League - 2020 - FM(2020)>, 'D:\\MetaData\\AFC\\AFC\\AFC_Champions_League_Elite_2020_events.xlsx')
(<Season: AFC Champions League - 2019 - FM(2019)>, 'D:\\MetaData\\AFC\\AFC\\AFC_Champions_League_Elite_2019_events.xlsx')
(<Season: AFC Champions League - 2018 - FM(2018)>, 'D:\\MetaData\\AFC\\AFC\\AFC_Champions_League_Elite_2018_events.xlsx')
(<Season: AFC Champions League 2 - 2024/2025 - FM(2024/2025)>, 'D:\\MetaData\\AFC\\AFC\\AFC_Champions_League_Two_202

FileNotFoundError: [Errno 2] No such file or directory: 'D:\\MetaData\\AFC\\India\\Indian_Super_League_2025_2026_events.xlsx'

mapped items

In [21]:
merged_data_collection = []
BASE_MERGE_DATA="D:/Merged_Items"
err,done=0,0
for i,(season,event_path,shot_path) in enumerate(map_example):
    print(f"Working on {i}/{len(map_example)} | Completed : {done} | Failed {err} | {season.name}")
    try :
        e_df = pd.read_excel(event_path).sort_values(['datetime','home_team','away_team'])
        # s_df = pd.read_excel(shot_path).sort_values(['datetime','home_team','away_team'])
        s_df = pd.concat([pd.read_excel(x) for x in shot_path.split("__||__")])
        event_teams = list(set(e_df['home_team'].to_list()+e_df['away_team'].to_list()))
        shot_teams = list(set(s_df['home_team'].to_list()+s_df['away_team'].to_list()))
    
        conf = season.competition.confederation
        country = season.competition.country
        name = season.competition.competition_name
        df,corr,wrong,ups = match_and_count_for_season(e_df,s_df,event_teams,shot_teams,11,return_counts=False)
        # print("Merging Done !!")
        print(f"df : {df.shape[0]}/{e_df.shape[0]}/{s_df.shape[0]} | corr : {corr} | wrong : {wrong} | ups : {ups} \n")
        # continue
        os.makedirs(BASE_MERGE_DATA, exist_ok=True)
        os.makedirs(f"{BASE_MERGE_DATA}/{conf}", exist_ok=True)
        os.makedirs(f"{BASE_MERGE_DATA}/{conf}/{country}", exist_ok=True)
        merge_path = f"{BASE_MERGE_DATA}/{conf}/{country}/{name.replace(' ','_')}__{season.name_fotmob.replace('/','_').replace(' - ','_').replace(' ','_').replace('-','_')}__Merged.xlsx"
        df.to_excel(merge_path,index=False)
        
        temp = {}
        temp['season'] = season
        temp['competition'] = f"{season.competition.competition_name}"
        temp['season_name'] = f"{season.name_fotmob}"
        
        
        temp['events_count'] = e_df.shape[0]
        temp['shot_count'] = s_df.shape[0]
        temp['merged_count'] = s_df.shape[0]
    
        temp['events_path'] = event_path
        temp['shot_path'] = shot_path
        temp['merged_path'] = merge_path
        merged_data_collection.append(temp)
        print(f"Completed '{season.competition.competition_name} | {season.name_fotmob}'")
        done+=1
    except Exception as e :
        print(f"Failed '{season.competition.competition_name} | {season.name_fotmob}'")
        print(e)
        err+=1

Working on 0/199 | Completed : 0 | Failed 0 | 2024/2025
df : 176/176/176 | corr : 176 | wrong : 0 | ups : 0 

Completed 'A-League | 2024/2025'
Working on 1/199 | Completed : 1 | Failed 0 | 2023/2024
df : 169/169/169 | corr : 169 | wrong : 0 | ups : 0 

Completed 'A-League | 2023/2024'
Working on 2/199 | Completed : 2 | Failed 0 | 2022/2023
df : 163/163/163 | corr : 163 | wrong : 0 | ups : 0 

Completed 'A-League | 2022/2023'
Working on 3/199 | Completed : 3 | Failed 0 | 2021/2022
df : 163/163/163 | corr : 163 | wrong : 0 | ups : 0 

Completed 'A-League | 2021/2022'
Working on 4/199 | Completed : 4 | Failed 0 | 2020/2021
df : 161/161/161 | corr : 161 | wrong : 0 | ups : 0 

Completed 'A-League | 2020/2021'
Working on 5/199 | Completed : 5 | Failed 0 | 2019/2020
df : 147/147/148 | corr : 147 | wrong : 0 | ups : 0 

Completed 'A-League | 2019/2020'
Working on 6/199 | Completed : 6 | Failed 0 | 2018/2019
df : 140/140/140 | corr : 140 | wrong : 0 | ups : 0 

Completed 'A-League | 2018/2019'

In [18]:
done,err,len(merged_data_collection)

(199, 0, 199)

In [19]:
merged_data_collection[0]

{'competition': 'A-League',
 'season': '2024/2025',
 'events_count': 176,
 'shot_count': 176,
 'merged_count': 176,
 'events_path': 'D:\\MetaData\\AFC\\Australia\\A-League_Men_2024_2025_events.xlsx',
 'shot_path': 'D:\\MetaData-shot\\AFC\\Australia\\A-League_2024_2025_shots.xlsx',
 'merged_path': 'D:/Merged_Items/AFC/Australia/A-League__2024_2025__Merged.xlsx'}

In [33]:
existing = []
errs=[]
for i,sns in enumerate(merged_data_collection,1) :
    m_df = pd.read_excel(sns.get('merged_path'))
    print(f"\nWorking on season no: {i} having {m_df.shape[0]} rows\n")
    for j,(_,row) in enumerate(m_df.iterrows(),1):
        try :
            obj,created = Game.objects.get_or_create(
                    season = sns.get('season'),
                    home_team = row.get('e_home_team'),
                    away_team = row.get('e_away_team'),
                    match_date = datetime.strptime(str(row.get('e_datetime')),"%Y-%m-%d %H:%M:%S"),
                    game_event_url = row.get('event_url'),
                    game_shot_url = row.get('shot_url')
            )
            if created is False :
                existing.append({
                    "season" : season,
                    "home_team" : row.get('e_home_team'),
                    "away_team" : row.get('e_away_team'),
                    "match_date" : datetime.strptime(str(row.get('e_datetime')),"%Y-%m-%d %H:%M:%S"),
                    "previous" : obj.__dict__,
                    "current" : dict(row)
                })
     
        except Exception as e :
            temp = {}
            temp['row'] = row
            temp['mg_path'] = sns.get('merged_path')
            temp['exception'] = e
            errs.append(temp)
    print(f"\tCompletion rate : {round((j/m_df.shape[0])*100,2)}%\n")



Working on season no: 1 having 176 rows

	Completion rate : 100.0%


Working on season no: 2 having 169 rows



D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2024-10-18 14:05:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2024-10-19 09:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2024-10-19 11:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2024-10-19 14:05:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\d

	Completion rate : 100.0%


Working on season no: 3 having 163 rows



D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2022-10-22 11:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2022-10-22 14:15:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2022-10-23 09:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2022-10-23 11:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\d

	Completion rate : 100.0%


Working on season no: 4 having 163 rows



...

D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2021-08-01 00:15:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2021-08-01 17:00:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2021-08-01 19:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2021-08-01 22:00:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\d

	Completion rate : 100.0%


Working on season no: 97 having 330 rows



D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2020-08-10 00:15:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2020-08-10 22:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2020-08-14 22:30:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\db\models\fields\__init__.py:1671: RuntimeWarning: DateTimeField Game.match_date received a naive datetime (2020-08-15 20:00:00) while time zone support is active.
  warnings.warn(
D:\Analysis_Portfolio\my-venv\Lib\site-packages\django\d

	Completion rate : 100.0%


Working on season no: 98 having 0 rows



ZeroDivisionError: division by zero

In [32]:
obj.id

1712

In [35]:
existing

[{'season': <Season: Liga MX - 2020/2021 - FM(2020/2021 - Clausura)>,
  'home_team': 'Central Coast Mariners FC',
  'away_team': 'Melbourne Victory FC',
  'match_date': datetime.datetime(2024, 10, 18, 14, 5),
  'previous': {'_state': <django.db.models.base.ModelState at 0x272d1186890>,
   'id': 1537,
   'season_id': 15,
   'home_team': 'Central Coast Mariners FC',
   'away_team': 'Melbourne Victory FC',
   'match_date': datetime.datetime(2024, 10, 18, 14, 5, tzinfo=datetime.timezone.utc),
   'event_status': 'not_done',
   'game_event_url': 'https://www.scoresway.com/en_GB/soccer/a-league-men-2024-2025/4yylure37f3rnsje6vmsps2s4/match/view/a7wz8r70htueolpgeewo3jok4/player-stats',
   'game_shot_url': 'https://www.fotmob.com/matches/melbourne-victory-vs-central-coast-mariners/1pop77#4587625'},
  'current': {'e_home_team': 'Central Coast Mariners FC',
   's_home_team': 'Central Coast Mariners',
   'e_away_team': 'Melbourne Victory FC',
   's_away_team': 'Melbourne Victory',
   'e_datetime':